In [1]:
import pandas as pd
import numpy as np 
import os 
from googletrans import Translator

In [2]:
rev = pd.read_csv('../madrid/reviews_detailed/comments_short.csv')

In [3]:
rev.head(100)

listing_id         id        date  reviewer_id  \
0         6369      29428  2010-03-14        84790   
1         6369      31018  2010-03-23        84338   
2         6369      34694  2010-04-10        98655   
3         6369      37146  2010-04-21       109871   
4         6369      38168  2010-04-26        98901   
..         ...        ...         ...          ...   
95       21853  273473012  2018-06-06     21220489   
96       21853  277764607  2018-06-17    182841821   
97       21853  290844505  2018-07-15     49900000   
98       24805   23330835  2014-11-29      9091591   
99       24805  166396094  2017-07-03      2704944   

                                             comments idiomas  \
0   simon and arturo have the ultimate location in...      en   
1   myself and kristy originally planned on stayin...      en   
2   we had a great time at arturo and simon's ! a ...      en   
3   i very much enjoyed the stay.  \r\nit's a wond...      en   
4   arturo and simon are polite and friendly hosts...      en   
..                                                ...     ...   
95  je recommande le logement de abdel. tout d'abo...      fr   
96                             muy buen alojamiento!       es   
97  abdel es muy buen anfitrin, est atento y dispo...      es   
98  during my stay, i enjoyed all around and had a...      en   
99  its very nice apartament, close to gran via, z...      en   

                                       comments_short  
0   arturo ultimate location step bus line want vi...  
1   plan stay arturo week plan change arturo open ...  
2   great time arturo cosy apartment wonderful ter...  
3   enjoy stay wonderful room bath great apartment...  
4   polite friendly host provide pleasant convenie...  
..                                                ...  
95  recommander logement abdel trs attentionn voul...  
96                                        alojamiento  
97  abdel anfitrin atento disponible cosa necesit ...  
98  stay enjoy fun area location apartment fantast...  
99        nice apartament close gran subway recommend  

[100 rows x 7 columns]

In [4]:
print(rev.isna().sum())

listing_id           0
id                   0
date                 0
reviewer_id          0
comments             0
idiomas              0
comments_short    2785
dtype: int64


In [5]:
rev = rev.dropna()

In [6]:
print(rev.isna().sum())

listing_id        0
id                0
date              0
reviewer_id       0
comments          0
idiomas           0
comments_short    0
dtype: int64


In [7]:
""""
from mtranslate import translate
# crear una muestra del dataframe con los primeros 100 comentarios
#rev_sample = rev.head(100).copy()

# definir la función de traducción
def translate_to_english(text):
    return translate(text, 'en')

# aplicar la función de traducción a la columna "comments_short" de la muestra
#rev_sample['comments_english'] = rev_sample['comments_short'].apply(translate_to_english)

# combinar la muestra traducida con el dataframe original
#rev = pd.concat([rev_sample, rev.iloc[100:]])

# imprimir los primeros 5 comentarios originales y sus traducciones al inglés
#print(pd.concat([rev_sample['comments_short'].head(100), rev_sample['comments_english'].head(100)], axis=1))

SyntaxError: EOF while scanning triple-quoted string literal (3811308782.py, line 17)

In [8]:



import requests
import pandas as pd
from tqdm import tqdm

# Función para traducir un texto a un idioma específico
def translate_text(text, lang, api_key):
    if lang != 'en':  # no traducir comentarios en inglés
        try:
            url = f'https://api.mymemory.translated.net/get?q={text}&langpair={lang}|en&key={api_key}'
            response = requests.get(url)
            if response.status_code == 200:
                translated_text = response.json()['responseData']['translatedText']
                return translated_text
            else:
                print(f"Error en la traducción. Código de estado HTTP: {response.status_code}")
        except Exception as e:
            print(f"Error en la traducción: {e}")
    else:
        return text

# Clave de la API
api_key = 'da62ac5334af060255a9'

# Tamaño de cada muestra
n = 100

# Dividir el dataframe en muestras más pequeñas
rev_chunks = [rev[i:i+n] for i in range(0, rev.shape[0], n)]

# Procesar cada muestra y agregar la columna "comments_english"
for i, chunk in enumerate(tqdm(rev_chunks, desc="Procesando muestras")):
    # Filtrar las filas que no están en inglés
    non_english_rows = chunk[chunk['idiomas'] != 'en']
    # Aplicar la función translate_text() a los comentarios que no están en inglés
    non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
    # Combinar los comentarios en inglés con los comentarios originales en inglés
    english_rows = chunk[chunk['idiomas'] == 'en'][['comments_short']]
    english_rows['comments_english'] = english_rows['comments_short']
    # Unir los comentarios en inglés recién traducidos con los comentarios originales en inglés
    chunk_with_english_comments = pd.concat([non_english_rows, english_rows], axis=0)
    chunk_with_english_comments.reset_index(drop=True, inplace=True)
    # Agregar la muestra procesada al dataframe general
    if i == 0:
        rev = chunk_with_english_comments.copy()
    else:
        rev = pd.concat([rev, chunk_with_english_comments], axis=0, ignore_index=True)

# Imprimir los primeros 5 comentarios originales y sus traducciones al inglés de la última muestra procesada
print(pd.concat([chunk_with_english_comments['comments_short'].head(), chunk_with_english_comments['comments_english'].head()], axis=1))


Procesando muestras:   0%|                                                                    | 0/6764 [00:00<?, ?it/s]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
Procesando muestras:   0%|                                                          | 1/6764 [00:03<6:19:22,  3.37s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentatio

Procesando muestras:   0%|                                                         | 13/6764 [01:02<7:29:52,  4.00s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
Procesando muestras:   0%|                                                         | 14/6764 [01:06<7:22:16,  3.93s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentatio

Procesando muestras:   0%|▏                                                       | 26/6764 [02:29<14:57:27,  7.99s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
Procesando muestras:   0%|▏                                                       | 27/6764 [02:32<12:24:38,  6.63s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentatio

Procesando muestras:   1%|▎                                                        | 39/6764 [03:26<8:47:08,  4.70s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
Procesando muestras:   1%|▎                                                        | 40/6764 [03:31<9:21:22,  5.01s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentatio

Procesando muestras:   1%|▍                                                        | 52/6764 [04:47<8:49:18,  4.73s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
Procesando muestras:   1%|▍                                                        | 53/6764 [04:51<8:39:17,  4.64s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentatio

...

Procesando muestras:  99%|█████████████████████████████████████████████████████▌| 6714/6764 [16:44:39<08:39, 10.39s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
Procesando muestras:  99%|█████████████████████████████████████████████████████▌| 6715/6764 [16:44:48<08:06,  9.93s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentatio

Procesando muestras:  99%|█████████████████████████████████████████████████████▋| 6727/6764 [16:46:51<06:08,  9.96s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
Procesando muestras:  99%|█████████████████████████████████████████████████████▋| 6728/6764 [16:47:02<06:09, 10.25s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentatio

Procesando muestras: 100%|█████████████████████████████████████████████████████▊| 6740/6764 [16:49:25<04:44, 11.86s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
Procesando muestras: 100%|█████████████████████████████████████████████████████▊| 6741/6764 [16:49:38<04:39, 12.14s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentatio

Procesando muestras: 100%|█████████████████████████████████████████████████████▉| 6753/6764 [16:51:58<02:06, 11.49s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_english_rows['comments_english'] = non_english_rows.apply(lambda x: translate_text(x['comments_short'], x['idiomas'], api_key), axis=1)
Procesando muestras: 100%|█████████████████████████████████████████████████████▉| 6754/6764 [16:52:11<02:00, 12.04s/it]C:\Users\Pedro Vidales\AppData\Local\Temp\ipykernel_9804\324492753.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentatio

                                      comments_short  \
0          excelente hospitalidad servicio respuesta   
1  raul sper atento momento tener problema vuelo ...   
2                      espacio ubicacin espectacular   
3  experencia inolvidable airbnb duda flo clment ...   
4  appartemer propre attractif prime terrasse chi...   

                                    comments_english  
0  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...  
1  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...  
2  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...  
3  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...  
4  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...  


In [9]:
rev.head()

listing_id          id        date  reviewer_id  \
0      6369.0  67786575.0  2016-03-31   26050860.0   
1      6369.0  68598541.0  2016-04-05    5199777.0   
2     21853.0  21051116.0  2014-10-10    8506071.0   
3     21853.0  22684525.0  2014-11-11   23357657.0   
4     21853.0  22871843.0  2014-11-16    4072731.0   

                                            comments idiomas  \
0  arturo est trs sympa et nous avons t trs bien ...      fr   
1  trs bon accueil de arturo. appartement trs spa...      fr   
2  mi experiencia en casa de adel fue buena, aunq...      es   
3  adel fue muy amable, incluso el da de mi llega...      es   
4  abdel ha sido un magnfico anfitrin y la mejor ...      es   

                                      comments_short  \
0  sympa tr chambre salle bain conformer photo tr...   
1  tr bon accueil appartemer spacieux terrass mag...   
2  experiencia casa principio costo ponerno entra...   
3  adel amable llegada salida metro ayud equipaje...   
4  abdel magnfico anfitrin forma ocurrir describi...   

                                    comments_english  
0  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...  
1  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...  
2  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...  
3  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...  
4  AUTHENTICATION FAILURE. TIP: DO NOT USE 'KEY' ...

In [ ]:
"""""
from tqdm import tqdm
from textblob import TextBlob

def translate_to_english(text):
    if isinstance(text, list):
        text = ' '.join(text)
    blob = TextBlob(text)
    return str(blob.translate(to='en'))

# dividir el dataframe en muestras más pequeñas
n = 100 # tamaño de cada muestra
rev_chunks = [rev[i:i+n] for i in range(0, rev.shape[0], n)]

# procesar cada muestra y agregar la columna "comments_english"
for i, chunk in enumerate(tqdm(rev_chunks, desc="Procesando muestras")):
    # filtar las filas que no son 'en' en la columna 'idiomas'
    non_english_rows = chunk[chunk['idiomas'] != 'en']
    # traducir los comentarios que no están en inglés
    non_english_rows['comments_english'] = non_english_rows['comments_short'].apply(translate_to_english)
    # combinar los comentarios en inglés recién traducidos con los comentarios originales en inglés
    english_rows = chunk[chunk['idiomas'] == 'en'][['comments_short']]
    english_rows['comments_english'] = english_rows['comments_short']
    # unir los comentarios en inglés recién traducidos con los comentarios originales en inglés
    chunk_with_english_comments = pd.concat([non_english_rows, english_rows], axis=0)
    chunk_with_english_comments.reset_index(drop=True, inplace=True)
    # agregar la muestra procesada al dataframe general
    if i == 0:
        rev = chunk_with_english_comments.copy()
    else:
        rev = pd.concat([rev, chunk_with_english_comments], axis=0, ignore_index=True)

    # imprimir los primeros 5 comentarios originales y sus traducciones al inglés de la última muestra procesada
    if i == len(rev_chunks) - 1:
        print(pd.concat([chunk_with_english_comments['comments_short'].head(), chunk_with_english_comments['comments_english'].head()], axis=1))
        
    
    """


In [ ]:
""""
from tqdm import tqdm

def translate_to_english(text):
    text_bytes = text.encode('utf-8')
    return translate(text_bytes, 'en')

# dividir el dataframe en muestras más pequeñas
n = 100 # tamaño de cada muestra
rev_chunks = [rev[i:i+n] for i in range(0, rev.shape[0], n)]

# procesar cada muestra y agregar la columna "comments_english"
for i, chunk in enumerate(tqdm(rev_chunks, desc="Procesando muestras")):
    # filtar las filas que no son 'en' en la columna 'idiomas'
    non_english_rows = chunk[chunk['idiomas'] != 'en']
    # traducir los comentarios que no están en inglés
    non_english_rows['comments_english'] = non_english_rows['comments_short'].apply(translate_to_english)
    # combinar los comentarios en inglés recién traducidos con los comentarios originales en inglés
    english_rows = chunk[chunk['idiomas'] == 'en'][['comments_short']]
    english_rows['comments_english'] = english_rows['comments_short']
    # unir los comentarios en inglés recién traducidos con los comentarios originales en inglés
    chunk_with_english_comments = pd.concat([non_english_rows, english_rows], axis=0)
    chunk_with_english_comments.reset_index(drop=True, inplace=True)
    # agregar la muestra procesada al dataframe general
    if i == 0:
        rev = chunk_with_english_comments.copy()
    else:
        rev = pd.concat([rev, chunk_with_english_comments], axis=0, ignore_index=True)

    # imprimir los primeros 5 comentarios originales y sus traducciones al inglés de la última muestra procesada
    if i == len(rev_chunks) - 1:
        print(pd.concat([chunk_with_english_comments['comments_short'].head(), chunk_with_english_comments['comments_english'].head()], axis=1))
        
        """

In [ ]:
""""
from tqdm import tqdm

# definir la función de traducción
def translate_to_english(text):
    text_bytes = text.encode('utf-8')
    return translate(text_bytes, 'en')

# dividir el dataframe en muestras más pequeñas
n = 100 # tamaño de cada muestra
rev_chunks = [rev[i:i+n] for i in range(0, rev.shape[0], n)]

# procesar cada muestra y agregar la columna "comments_english"
for i, chunk in enumerate(tqdm(rev_chunks, desc="Procesando muestras")):
    chunk['comments_english'] = chunk['comments_short'].apply(translate_to_english)

# unir los resultados de cada muestra en un solo dataframe
rev = pd.concat(rev_chunks, axis=0, ignore_index=True)

# imprimir los primeros 5 comentarios originales y sus traducciones al inglés
print(pd.concat([rev['comments_short'].head(), rev['comments_english'].head()], axis=1))

""""

In [ ]:
da62ac5334af060255a9